In [1]:
import pandas as pd

# Load data
transactions = pd.read_csv('/Users/maxandchang/Documents/jobs/Appostrophe/case-study-transactions.csv')
installs = pd.read_csv('/Users/maxandchang/Documents/jobs/Appostrophe/case-study-installs.csv')

In [26]:
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go

In [30]:
# Convert transaction_date and install_date to datetime
transactions['transaction_date'] = pd.to_datetime(transactions['transaction_date'])
installs['install_date'] = pd.to_datetime(installs['install_date'])

# Convert 'segment' column to string data type and add 'segment' in front of each value
installs['segment'] = 'segment' + installs['segment'].astype(str)

In [46]:
# Get unique user_ids from transactions
trans_id = transactions['user_id'].unique()

# Check if 'user_id' in 'installs' is found in 'trans_id'
installs['purchase'] = installs['user_id'].isin(trans_id).map({True: 'Yes', False: 'No'})

# Display the updated installs dataframe
print(installs.head())



   user_id   segment install_date purchase
0        1  segment2   2023-09-01       No
1        2  segment2   2023-09-02       No
2        3  segment0   2023-09-25       No
3        4  segment1   2023-09-09       No
4        5  segment1   2023-09-09      Yes


In [55]:
# Define the color palette
color_palette = ['rgb(31, 119, 180)', 'rgb(255, 127, 14)', 'rgb(44, 160, 44)', 'rgb(214, 39, 40)', 
                 'rgb(148, 103, 189)', 'rgb(140, 86, 75)', 'rgb(227, 119, 194)', 'rgb(127, 127, 127)', 
                 'rgb(188, 189, 34)']

# Create the histogram with the specified color palette
fig_installs = px.histogram(installs, x="install_date", color='segment', opacity=0.7,
                            color_discrete_sequence=color_palette,
                            pattern_shape="purchase",
                            pattern_shape_sequence=["", "x"])

# Show the histogram
fig_installs.update_layout(bargap=0.1)
fig_installs.update_traces(marker_pattern_size=5, selector=dict(type='histogram'))
fig_installs.show()

In [57]:
# Calculate percentage of 'Yes' under 'purchase' grouped by 'segment'
purchase_percentage = installs.groupby('segment')['purchase'].value_counts(normalize=True) * 100
purchase_percentage

segment   purchase
segment0  No          89.879825
          Yes         10.120175
segment1  No          90.002790
          Yes          9.997210
segment2  No          90.203227
          Yes          9.796773
Name: purchase, dtype: float64

In [105]:
transactions['price_in_usd'] = transactions['price_in_usd'].fillna(0)

In [107]:
# Merge dataframes on user_id keeping all rows
data_merge = pd.merge(installs, transactions, on='user_id', how='inner')

# Create a new column 'status' by combining the first letters from 'is_free_trial' and 'is_conversion_to_pay'
data_merge['status'] = data_merge['is_free_trial'].astype(str).str[0] + \
                        data_merge['is_conversion_to_pay'].astype(str).str[0] + \
                        data_merge['price_in_usd'].astype(str)
data_merge.head()


user_id   segment install_date purchase transaction_date  is_free_trial  \
0        5  segment1   2023-09-09      Yes       2023-09-09           True   
1       10  segment0   2023-09-19      Yes       2023-09-19           True   
2       10  segment0   2023-09-19      Yes       2023-09-26          False   
3       22  segment1   2023-09-04      Yes       2023-09-04           True   
4       22  segment1   2023-09-04      Yes       2023-09-11          False   

   is_conversion_to_pay  price_in_usd  status  
0                 False          0.00   TF0.0  
1                 False          0.00   TF0.0  
2                  True          2.99  FT2.99  
3                 False          0.00   TF0.0  
4                  True          2.99  FT2.99

In [205]:
data_merge_unique['segment'].value_counts()

segment0    5078
segment1    5016
segment2    4864
Name: segment, dtype: int64

In [144]:
fig_transaction = px.histogram(data_merge, y='status', color='status', opacity=0.7,
                            color_discrete_sequence=color_palette,
                            facet_row="segment")
fig_transaction.for_each_annotation(lambda a: a.update(text=a.text.split("=")[-1]))
fig_transaction.show()

In [163]:
data_merge['user_id'] = data_merge['user_id'].astype(str)

In [170]:
fig_transaction2 = px.histogram(data_merge, x='user_id', color='status', opacity=0.7,
                            color_discrete_sequence=color_palette,
                            facet_row="segment",
                            category_orders={"segment": ["segment0", "segment1", "segment2"]})
fig_transaction2.for_each_annotation(lambda a: a.update(text=a.text.split("=")[-1]))
fig_transaction2.update_xaxes(matches=None)
fig_transaction2.show()

In [174]:
# Sort the dataframe by 'user_id' and 'transaction_date'
# Sort the dataframe by 'segment' and 'transaction_date'
data_merge_sorted = data_merge.sort_values(by=['segment', 'transaction_date'])
# Calculate the re_id based on the earliest 'transaction_date' within each segment
data_merge_sorted['re_id'] = data_merge_sorted.groupby('segment')['user_id'].rank(method='dense')

data_merge_sorted.head(n=10)

user_id   segment install_date purchase transaction_date  is_free_trial  \
238      796  segment0   2023-09-01      Yes       2023-09-01           True   
1248    4981  segment0   2023-09-01      Yes       2023-09-01           True   
1319    5355  segment0   2023-09-01      Yes       2023-09-01           True   
1645    6639  segment0   2023-09-01      Yes       2023-09-01           True   
1780    7258  segment0   2023-09-01      Yes       2023-09-01           True   
1809    7381  segment0   2023-09-01      Yes       2023-09-01           True   
2051    8406  segment0   2023-09-01      Yes       2023-09-01           True   
2170    8829  segment0   2023-09-01      Yes       2023-09-01           True   
2339    9222  segment0   2023-09-01      Yes       2023-09-01           True   
2530   10061  segment0   2023-09-01      Yes       2023-09-01           True   

      is_conversion_to_pay  price_in_usd status   re_id  
238                  False           0.0  TF0.0  4300.0  
1248                 False           0.0  TF0.0  3153.0  
1319                 False           0.0  TF0.0  3289.0  
1645                 False           0.0  TF0.0  3802.0  
1780                 False           0.0  TF0.0  4042.0  
1809                 False           0.0  TF0.0  4081.0  
2051                 False           0.0  TF0.0  4459.0  
2170                 False           0.0  TF0.0  4625.0  
2339                 False           0.0  TF0.0  4797.0  
2530                 False           0.0  TF0.0    28.0

In [111]:
# Summarize the 'status' column
status_summary = data_merge['status'].value_counts()
status_summary

FF2.99    18418
TF0.0     14958
FT2.99     7443
Name: status, dtype: int64

In [127]:
transaction_date_description = data_merge['transaction_date'].describe()

# Find the newest date
newest_date = transaction_date_description['last']

# Find the earliest date
earliest_date = transaction_date_description['first']

print("Newest Date:", newest_date)
print("Earliest Date:", earliest_date)

# Calculate the number of days between the first and last dates
days_between = (newest_date - earliest_date).days

# Print the result
print("Number of days between the first and last dates:", days_between)


Newest Date: 2024-03-25 00:00:00
Earliest Date: 2023-09-01 00:00:00
Number of days between the first and last dates: 206


/Users/maxandchang/Documents/JupyterBook/jupyterbook/lib/python3.7/site-packages/ipykernel_launcher.py:1: FutureWarning:

Treating datetime data as categorical rather than numeric in `.describe` is deprecated and will be removed in a future version of pandas. Specify `datetime_is_numeric=True` to silence this warning and adopt the future behavior now.



In [185]:
# Remove duplicates based on 'user_id' column and keep the first appearance
data_merge_unique = data_merge.drop_duplicates(subset=['user_id'])

# Sort the dataframe by 'segment' and 'transaction_date'
data_merge_unique_sorted = data_merge_unique.sort_values(by=['segment', 'transaction_date'])

# Re id
data_merge_unique_sorted['re_id'] = data_merge_unique_sorted.groupby('segment')['transaction_date'].rank(method='first')

# data_merge_unique_sorted['re_id'] = data_merge_unique_sorted['re_id'].astype(str)
data_merge_unique_sorted = data_merge_unique_sorted[['user_id', 're_id']]

data_merge2 = pd.merge(data_merge, data_merge_unique_sorted, on='user_id', how='left')
data_merge2.head()


user_id   segment install_date purchase transaction_date  is_free_trial  \
0       5  segment1   2023-09-09      Yes       2023-09-09           True   
1      10  segment0   2023-09-19      Yes       2023-09-19           True   
2      10  segment0   2023-09-19      Yes       2023-09-26          False   
3      22  segment1   2023-09-04      Yes       2023-09-04           True   
4      22  segment1   2023-09-04      Yes       2023-09-11          False   

   is_conversion_to_pay  price_in_usd  status   re_id  
0                 False          0.00   TF0.0  1238.0  
1                 False          0.00   TF0.0  3042.0  
2                  True          2.99  FT2.99  3042.0  
3                 False          0.00   TF0.0   424.0  
4                  True          2.99  FT2.99   424.0

In [195]:
fig_transaction2 = px.histogram(data_merge2, x='re_id', color='status', opacity=0.7,
                            color_discrete_sequence=color_palette,
                            facet_row="segment",
                            category_orders={"segment": ["segment0", "segment1", "segment2"]},
                            hover_data='user_id'
        )
fig_transaction2.for_each_annotation(lambda a: a.update(text=a.text.split("=")[-1]))
#fig_transaction2.update_xaxes(matches=None)
fig_transaction2.update_traces(xbins=dict( size=1))
fig_transaction2.show()

In [199]:
# Count the occurrences of each user_id
user_id_counts = data_merge['user_id'].value_counts()

# Create a new column based on the condition
data_merge['payment_status'] = data_merge['user_id'].map(user_id_counts).apply(lambda x: 'nonpay' if x == 1 else 'pay')

# Keep only the first occurrence of each user_id
data_merge_first = data_merge.drop_duplicates(subset='user_id', keep='first')

data_merge_first.head(n=10)

user_id   segment install_date purchase transaction_date  is_free_trial  \
0        5  segment1   2023-09-09      Yes       2023-09-09           True   
1       10  segment0   2023-09-19      Yes       2023-09-19           True   
3       22  segment1   2023-09-04      Yes       2023-09-04           True   
9       34  segment2   2023-09-22      Yes       2023-09-22           True   
12      40  segment2   2023-09-16      Yes       2023-09-16           True   
13      46  segment0   2023-09-24      Yes       2023-09-24           True   
19      48  segment1   2023-09-17      Yes       2023-09-17           True   
21      50  segment1   2023-09-02      Yes       2023-09-02           True   
23      58  segment2   2023-09-08      Yes       2023-09-08           True   
24      59  segment2   2023-09-17      Yes       2023-09-17           True   

    is_conversion_to_pay  price_in_usd status payment_status  
0                  False           0.0  TF0.0         nonpay  
1                  False           0.0  TF0.0            pay  
3                  False           0.0  TF0.0            pay  
9                  False           0.0  TF0.0            pay  
12                 False           0.0  TF0.0         nonpay  
13                 False           0.0  TF0.0            pay  
19                 False           0.0  TF0.0            pay  
21                 False           0.0  TF0.0            pay  
23                 False           0.0  TF0.0         nonpay  
24                 False           0.0  TF0.0            pay

In [201]:
fig_transaction = px.histogram(data_merge_first, x='segment', color='segment', opacity=0.7,
                            color_discrete_sequence=color_palette,
                            category_orders={"segment": ["segment0", "segment1", "segment2"]},
                            pattern_shape="payment_status",
                            pattern_shape_sequence=["", "x"]
        )
#fig_transaction.for_each_annotation(lambda a: a.update(text=a.text.split("=")[-1]))
#fig_transaction.update_xaxes(matches=None)
#fig_transaction.update_traces(xbins=dict( size=1))
fig_transaction.show()

In [160]:
# Count occurrences of each user_id
user_id_counts = data_merge['user_id'].value_counts()
# Filter out rows where user_id occurs only once
filtered_data_merge = data_merge[data_merge['user_id'].map(user_id_counts) == 1]
seg0 = data_merge[data_merge['segment'] == 'segment0']
seg0['status'].value_counts()

FF2.99    6249
TF0.0     5078
FT2.99    2536
Name: status, dtype: int64

In [114]:
# Summarize the 'status' column
status_summary_unique = data_merge_unique['status'].value_counts()
status_summary_unique

TF0.0    14958
Name: status, dtype: int64

## How many percentage pay at leat once after free-trial is over.

In [124]:
# Sort the dataframe by 'user_id' and 'transaction_date'
data_merge_sorted = data_merge.sort_values(by=['user_id', 'transaction_date'])
# Calculate the difference in days between consecutive rows within each group
data_merge_sorted['dayB2P'] = data_merge_sorted.groupby('user_id')['transaction_date'].diff().dt.days

user_id   segment install_date purchase transaction_date  is_free_trial  \
0        5  segment1   2023-09-09      Yes       2023-09-09           True   
1       10  segment0   2023-09-19      Yes       2023-09-19           True   
2       10  segment0   2023-09-19      Yes       2023-09-26          False   
3       22  segment1   2023-09-04      Yes       2023-09-04           True   
4       22  segment1   2023-09-04      Yes       2023-09-11          False   

   is_conversion_to_pay  price_in_usd  status  dayB2P  
0                 False          0.00   TF0.0     NaN  
1                 False          0.00   TF0.0     NaN  
2                  True          2.99  FT2.99     7.0  
3                 False          0.00   TF0.0     NaN  
4                  True          2.99  FT2.99     7.0

In [136]:
data_merge_filtered = data_merge_sorted[data_merge_sorted['transaction_date'] == '2024-03-25']
data_merge_filtered

user_id   segment install_date purchase transaction_date  \
8914     35189  segment0   2023-09-24      Yes       2024-03-25   
30782   112221  segment2   2023-09-24      Yes       2024-03-25   
32075   117075  segment2   2023-09-29      Yes       2024-03-25   

       is_free_trial  is_conversion_to_pay  price_in_usd  status  dayB2P  
8914           False                 False          2.99  FF2.99     7.0  
30782          False                 False          2.99  FF2.99    14.0  
32075          False                 False          2.99  FF2.99     7.0

In [125]:
data_merge_sorted['dayB2P'].unique()

array([nan,  7., 14., 21., 42., 35., 28., 49., 70.])

In [133]:
# Count the occurrences of each user_id
user_id_counts = data_merge['user_id'].value_counts()
# Calculate the number of unique user_id values that appear only once
single_appearances = (user_id_counts == 1).sum()
# Calculate the total number of unique user_id values
total_unique_user_ids = len(user_id_counts)
# Calculate the percentage of user_id values that appear only once
percentage_single_appearances = (single_appearances / total_unique_user_ids) * 100

print("Percentage of user_id values that appear only once:", percentage_single_appearances)

Percentage of user_id values that appear only once: 50.24067388688327


In [206]:
segment_user_id_counts = data_merge.groupby('segment')['user_id'].value_counts()

# Calculate the number of unique user_id values that appear only once in each segment group
segment_user_id_counts.groupby(level=0).apply(lambda x: (x != 1).sum())

segment
segment0    2536
segment1    2504
segment2    2403
Name: user_id, dtype: int64

In [134]:
# Count the occurrences of each user_id within each segment group
segment_user_id_counts = data_merge.groupby('segment')['user_id'].value_counts()

# Calculate the number of unique user_id values that appear only once in each segment group
segment_single_appearances = segment_user_id_counts.groupby(level=0).apply(lambda x: (x == 1).sum())

# Calculate the total number of unique user_id values in each segment group
segment_total_unique_user_ids = segment_user_id_counts.groupby(level=0).size()

# Calculate the percentage of user_id values that appear only once in each segment group
segment_percentage_single_appearances = (segment_single_appearances / segment_total_unique_user_ids) * 100

print("Percentage of user_id values that appear only once in each segment group:")
print(segment_percentage_single_appearances)


Percentage of user_id values that appear only once in each segment group:
segment
segment0    50.059078
segment1    50.079745
segment2    50.596217
Name: user_id, dtype: float64


In [209]:
# Group data_merge by user_id and calculate duration for each user
duration = data_merge.groupby('user_id')['transaction_date'].apply(lambda x: (x.max() - x.min()).days).values

duration


array([ 7,  7,  0, ...,  0,  0, 28])

In [212]:
# Get the indices that would sort the array
sorted_indices = np.argsort(duration)

# Use the sorted indices to reorder the array
sorted_duration = duration[sorted_indices]
sorted_duration[-10:] 

array([189, 189, 196, 196, 196, 196, 196, 196, 196, 196])

In [213]:
data_merge3 = data_merge2[data_merge2['payment_status'] == 'pay']
data_merge3.head()

KeyError: 'payment_status'